In [1]:
from replenishment import (
    build_percentile_forecast_candidates_from_standard_rows,
    build_point_forecast_article_configs_from_standard_rows,
    build_replenishment_decisions_from_optimization_results,
    build_replenishment_decisions_from_simulations,
    generate_standard_simulation_rows,
    optimize_aggregation_and_forecast_targets,
    optimize_aggregation_windows,
    optimize_forecast_targets,
    optimize_service_level_factors,
    replenishment_decision_rows_to_dataframe,
    split_standard_simulation_rows,
    simulate_replenishment_with_aggregation,
    standard_simulation_rows_to_dataframe,
)


In [2]:
rows = generate_standard_simulation_rows(
    n_unique_ids=300,
    periods=150,
    forecast_start_period=100,
    history_mean=18,
    history_std=4,
    forecast_mean=20,
    forecast_std=3,
    seed=7,
)
df = standard_simulation_rows_to_dataframe(rows, library="pandas")
df.head()


unique_id          ds  forecast  actuals  holding_cost_per_unit  \
0         A  2024-01-01        19     20.0                    0.5   
1         A  2024-01-31        19     17.0                    0.5   
2         A  2024-03-01        17     17.0                    0.5   
3         A  2024-03-31        23     20.0                    0.5   
4         A  2024-04-30        23     19.0                    0.5   

   stockout_cost_per_unit  order_cost_per_order  lead_time  initial_on_hand  \
0                     3.0                  12.5          1               30   
1                     3.0                  12.5          1               30   
2                     3.0                  12.5          1               30   
3                     3.0                  12.5          1               30   
4                     3.0                  12.5          1               30   

   current_stock  is_forecast  forecast_p50  forecast_p90  
0             30        False            19            24  
1             30        False            19            24  
2             30        False            17            21  
3             30        False            23            29  
4             30        False            23            29

In [3]:
backtest_rows, forecast_rows = split_standard_simulation_rows(rows)
point_configs = build_point_forecast_article_configs_from_standard_rows(
    backtest_rows,
    service_level_factor=0.9,
)
point_result = optimize_service_level_factors(
    point_configs,
    candidate_factors=[0.8, 0.9, 0.95],
)
point_result


{'A': PointForecastOptimizationResult(service_level_factor=0.8, simulation=SimulationResult(snapshots=[InventorySnapshot(period=0, starting_on_hand=30, demand=20, received=0, ending_on_hand=10, backorders=0, order_placed=19, on_order=19), InventorySnapshot(period=1, starting_on_hand=29, demand=17, received=19, ending_on_hand=12, backorders=0, order_placed=18, on_order=18), InventorySnapshot(period=2, starting_on_hand=30, demand=17, received=18, ending_on_hand=13, backorders=0, order_placed=25, on_order=25), InventorySnapshot(period=3, starting_on_hand=38, demand=20, received=25, ending_on_hand=18, backorders=0, order_placed=25, on_order=25), InventorySnapshot(period=4, starting_on_hand=43, demand=19, received=25, ending_on_hand=24, backorders=0, order_placed=23, on_order=23), InventorySnapshot(period=5, starting_on_hand=47, demand=19, received=23, ending_on_hand=28, backorders=0, order_placed=17, on_order=17), InventorySnapshot(period=6, starting_on_hand=45, demand=21, received=17, end

In [4]:
aggregation_result = optimize_aggregation_windows(
    point_configs,
    candidate_windows=[1, 2, 3, 4, 5, 6, 7],
)
best_factors = {
    unique_id: result.service_level_factor
    for unique_id, result in point_result.items()
}
forecast_point_configs = build_point_forecast_article_configs_from_standard_rows(
    forecast_rows,
    service_level_factor=best_factors,
)
forecast_simulations = {
    unique_id: simulate_replenishment_with_aggregation(
        periods=config.periods,
        demand=config.demand,
        initial_on_hand=config.initial_on_hand,
        lead_time=config.lead_time,
        policy=config.policy,
        aggregation_window=aggregation_result[unique_id].window,
        holding_cost_per_unit=config.holding_cost_per_unit,
        stockout_cost_per_unit=config.stockout_cost_per_unit,
        order_cost_per_order=config.order_cost_per_order,
        order_cost_per_unit=config.order_cost_per_unit,
    )
    for unique_id, config in forecast_point_configs.items()
}
decision_rows = build_replenishment_decisions_from_simulations(
    forecast_rows,
    forecast_simulations,
    aggregation_window={
        unique_id: aggregation_result[unique_id].window
        for unique_id in forecast_point_configs
    },
    sigma=best_factors,
)
replenishment_decision_rows_to_dataframe(decision_rows, library='pandas')


unique_id          ds  quantity sigma  aggregation_window  \
0            A  2032-03-19       131  None                   6   
1            A  2032-09-15       118  None                   6   
2            A  2033-03-14       131  None                   6   
3            A  2033-09-10       124  None                   6   
4            A  2034-03-09       107  None                   6   
...        ...         ...       ...   ...                 ...   
2472   SKU-300  2034-03-09       128  None                   6   
2473   SKU-300  2034-09-05       126  None                   6   
2474   SKU-300  2035-03-04       129  None                   6   
2475   SKU-300  2035-08-31        49  None                   6   
2476   SKU-300  2036-02-27        49  None                   6   

     percentile_target  
0                 None  
1                 None  
2                 None  
3                 None  
4                 None  
...                ...  
2472              None  
2473              None  
2474              None  
2475              None  
2476              None  

[2477 rows x 6 columns]

In [5]:
percentile_configs = build_percentile_forecast_candidates_from_standard_rows(backtest_rows)
percentile_result = optimize_forecast_targets(
    percentile_configs,
)


In [6]:
forecast_percentile_configs = build_percentile_forecast_candidates_from_standard_rows(
    forecast_rows,
)
joint_results = optimize_aggregation_and_forecast_targets(
    forecast_percentile_configs,
    candidate_windows=[5, 6, 7],
)

percentile_decision_rows = build_replenishment_decisions_from_optimization_results(
    forecast_rows,
    joint_results,
)
result_df = replenishment_decision_rows_to_dataframe(
    percentile_decision_rows,
    library='pandas',
)
result_df.head()


unique_id          ds  quantity sigma  aggregation_window percentile_target
0         A  2032-03-19       132  None                   5               p90
1         A  2032-08-16       126  None                   5               p90
2         A  2033-01-13       125  None                   5               p90
3         A  2033-06-12       135  None                   5               p90
4         A  2033-11-09       133  None                   5               p90